In [1]:
import logging
import pickle
import numpy as np
from openmmtools.integrators import PeriodicNonequilibriumIntegrator
from simtk import unit
from simtk import openmm
import argparse
import os
import time
import mdtraj as md
from simtk.openmm import XmlSerializer

In [35]:
# Set up logger
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

# Define lambda functions
x = 'lambda'
DEFAULT_ALCHEMICAL_FUNCTIONS = {
                             'lambda_sterics_core': x,
                             'lambda_electrostatics_core': x,
                             'lambda_sterics_insert': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_sterics_delete': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_insert': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_delete': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_bonds': x,
                             'lambda_angles': x,
                             'lambda_torsions': x}

# Define simulation parameters
# nsteps_eq = 250000 # 1 ns
# nsteps_neq = 250000 # 1 ns
nsteps_eq = 5000 # 10 ps
nsteps_neq = 5000 # 10 ps
neq_splitting='V R H O R V'
timestep = 2.0 * unit.femtosecond
platform_name = 'CUDA'

In [ ]:
# Read in htf
with open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN1/htf.npz", 'rb') as f:
    htf = np.load(f, allow_pickle=True)
    htf = htf.get('arr_0')
# system = htf.hybrid_system
# positions = htf.hybrid_positions


In [37]:
htf = htf.flatten()[0]

In [ ]:
htf.hybrid_topology.

In [ ]:
# Deserialize integrator file 
with open("/data/chodera/zhangi/perses_benchmark/fah/fah/17300/RUNS/RUN08/integrator.xml", 'r') as f:
    integrator = XmlSerializer.deserialize(f.read())

In [24]:
integrator

<simtk.openmm.openmm.CustomIntegrator; proxy of <Swig Object of type 'OpenMM::CustomIntegrator *' at 0x2b2efbf4bcc0> >

In [8]:
# Make and serialize and deserialize integrator

from openmmtools.integrators import PeriodicNonequilibriumIntegrator
integrator = PeriodicNonequilibriumIntegrator(DEFAULT_ALCHEMICAL_FUNCTIONS, nsteps_eq, nsteps_neq, neq_splitting, timestep=timestep)
from perses.utils import data
data.serialize(integrator, f"integrator.xml")
with open("integrator.xml", 'r') as f:
    integrator = XmlSerializer.deserialize(f.read())


In [46]:
# Make integrator
from openmmtools.integrators import PeriodicNonequilibriumIntegrator
integrator = PeriodicNonequilibriumIntegrator(DEFAULT_ALCHEMICAL_FUNCTIONS, nsteps_eq, nsteps_neq, neq_splitting, timestep=timestep)

In [39]:
# Deserialize system file 
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN03/system.xml.bz2", 'rb') as f:
    system = XmlSerializer.deserialize(f.read().decode("utf-8"))


In [40]:
# Set up context
platform_name = 'OpenCL'
platform = openmm.Platform.getPlatformByName(platform_name)
if platform_name in ['CUDA', 'OpenCL']:
    platform.setPropertyDefaultValue('Precision', 'mixed')
if platform_name in ['CUDA']:
    platform.setPropertyDefaultValue('DeterministicForces', 'true')
context = openmm.Context(system, integrator, platform)


In [41]:
# Load state and set box vectors, positions, and velocities
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN03/state.xml.bz2", 'rb') as infile:
    state = XmlSerializer.deserialize(infile.read().decode('utf-8'))
context.setPeriodicBoxVectors(*state.getPeriodicBoxVectors())
context.setPositions(state.getPositions())
context.setVelocities(state.getVelocities())


In [42]:
# Run neq
phase = 'complex'
i = 17300
ncycles = 1
forward_works_master, reverse_works_master = list(), list()
forward_eq_old, forward_neq_old, forward_neq_new = list(), list(), list()
reverse_eq_new, reverse_neq_old, reverse_neq_new = list(), list(), list()
for cycle in range(ncycles):
    # Equilibrium (lambda = 0)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 0, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            forward_eq_old.append(old_pos)

    # Forward (0 -> 1)
    forward_works = [integrator.get_protocol_work(dimensionless=True)]
    for fwd_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        forward_works.append(integrator.get_protocol_work(dimensionless=True))
        if fwd_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, forward NEQ step: {fwd_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            forward_neq_old.append(old_pos)
            forward_neq_new.append(new_pos)
    forward_works_master.append(forward_works)
    
    # Equilibrium (lambda = 1)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 1, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_eq_new.append(new_pos)

    # Reverse work (1 -> 0)
    reverse_works = [integrator.get_protocol_work(dimensionless=True)]
    for rev_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        reverse_works.append(integrator.get_protocol_work(dimensionless=True))
        if rev_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, reverse NEQ step: {rev_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_neq_old.append(old_pos)
            reverse_neq_new.append(new_pos)
    reverse_works_master.append(reverse_works)
        
#     # Save works
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward.npy"), 'wb') as f:
#         np.save(f, forward_works_master)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse.npy"), 'wb') as f:
#         np.save(f, reverse_works_master)

#     # Save trajs
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_eq_old.npy"), 'wb') as f:
#         np.save(f, forward_eq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_eq_new.npy"), 'wb') as f:
#         np.save(f, reverse_eq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_old.npy"), 'wb') as f:
#         np.save(f, forward_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_new.npy"), 'wb') as f:
#         np.save(f, forward_neq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_old.npy"), 'wb') as f:
#         np.save(f, reverse_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_new.npy"), 'wb') as f:
#         np.save(f, reverse_neq_new)



INFO:root:Cycle: 0, Step: 0, equilibrating at lambda = 0, took: 30.794672966003418 seconds
INFO:root:Cycle: 0, Step: 750, equilibrating at lambda = 0, took: 0.02004265785217285 seconds
INFO:root:Cycle: 0, Step: 1500, equilibrating at lambda = 0, took: 0.02026987075805664 seconds
INFO:root:Cycle: 0, Step: 2250, equilibrating at lambda = 0, took: 0.02022075653076172 seconds
INFO:root:Cycle: 0, Step: 3000, equilibrating at lambda = 0, took: 0.020285844802856445 seconds
INFO:root:Cycle: 0, Step: 3750, equilibrating at lambda = 0, took: 0.02016448974609375 seconds
INFO:root:Cycle: 0, Step: 4500, equilibrating at lambda = 0, took: 0.020317554473876953 seconds
INFO:root:Cycle: 0, forward NEQ step: 0, took: 0.019861221313476562 seconds
INFO:root:Cycle: 0, forward NEQ step: 750, took: 0.020069122314453125 seconds
INFO:root:Cycle: 0, forward NEQ step: 1500, took: 0.020242691040039062 seconds
INFO:root:Cycle: 0, forward NEQ step: 2250, took: 0.020135879516601562 seconds
INFO:root:Cycle: 0, forwar

Try to optimize performance -- relax constraint tolerance

In [47]:
integrator.setConstraintTolerance(1e-6)

In [48]:
# Deserialize system file 
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN03/system.xml.bz2", 'rb') as f:
    system = XmlSerializer.deserialize(f.read().decode("utf-8"))


In [49]:
# Set up context
platform_name = 'OpenCL'
platform = openmm.Platform.getPlatformByName(platform_name)
if platform_name in ['CUDA', 'OpenCL']:
    platform.setPropertyDefaultValue('Precision', 'mixed')
if platform_name in ['CUDA']:
    platform.setPropertyDefaultValue('DeterministicForces', 'true')
context = openmm.Context(system, integrator, platform)


In [50]:
# Load state and set box vectors, positions, and velocities
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN03/state.xml.bz2", 'rb') as infile:
    state = XmlSerializer.deserialize(infile.read().decode('utf-8'))
context.setPeriodicBoxVectors(*state.getPeriodicBoxVectors())
context.setPositions(state.getPositions())
context.setVelocities(state.getVelocities())


In [51]:
# Run neq
phase = 'complex'
i = 17300
ncycles = 1
forward_works_master, reverse_works_master = list(), list()
forward_eq_old, forward_neq_old, forward_neq_new = list(), list(), list()
reverse_eq_new, reverse_neq_old, reverse_neq_new = list(), list(), list()
for cycle in range(ncycles):
    # Equilibrium (lambda = 0)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 0, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            forward_eq_old.append(old_pos)

    # Forward (0 -> 1)
    forward_works = [integrator.get_protocol_work(dimensionless=True)]
    for fwd_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        forward_works.append(integrator.get_protocol_work(dimensionless=True))
        if fwd_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, forward NEQ step: {fwd_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            forward_neq_old.append(old_pos)
            forward_neq_new.append(new_pos)
    forward_works_master.append(forward_works)
    
    # Equilibrium (lambda = 1)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 1, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_eq_new.append(new_pos)

    # Reverse work (1 -> 0)
    reverse_works = [integrator.get_protocol_work(dimensionless=True)]
    for rev_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        reverse_works.append(integrator.get_protocol_work(dimensionless=True))
        if rev_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, reverse NEQ step: {rev_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_neq_old.append(old_pos)
            reverse_neq_new.append(new_pos)
    reverse_works_master.append(reverse_works)
        
#     # Save works
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward.npy"), 'wb') as f:
#         np.save(f, forward_works_master)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse.npy"), 'wb') as f:
#         np.save(f, reverse_works_master)

#     # Save trajs
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_eq_old.npy"), 'wb') as f:
#         np.save(f, forward_eq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_eq_new.npy"), 'wb') as f:
#         np.save(f, reverse_eq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_old.npy"), 'wb') as f:
#         np.save(f, forward_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_new.npy"), 'wb') as f:
#         np.save(f, forward_neq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_old.npy"), 'wb') as f:
#         np.save(f, reverse_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_new.npy"), 'wb') as f:
#         np.save(f, reverse_neq_new)



INFO:root:Cycle: 0, Step: 0, equilibrating at lambda = 0, took: 0.2146315574645996 seconds
INFO:root:Cycle: 0, Step: 750, equilibrating at lambda = 0, took: 0.020085573196411133 seconds
INFO:root:Cycle: 0, Step: 1500, equilibrating at lambda = 0, took: 0.020203828811645508 seconds
INFO:root:Cycle: 0, Step: 2250, equilibrating at lambda = 0, took: 0.02013850212097168 seconds
INFO:root:Cycle: 0, Step: 3000, equilibrating at lambda = 0, took: 0.020146608352661133 seconds
INFO:root:Cycle: 0, Step: 3750, equilibrating at lambda = 0, took: 0.019999027252197266 seconds
INFO:root:Cycle: 0, Step: 4500, equilibrating at lambda = 0, took: 0.020099163055419922 seconds
INFO:root:Cycle: 0, forward NEQ step: 0, took: 0.02005147933959961 seconds
INFO:root:Cycle: 0, forward NEQ step: 750, took: 0.0202023983001709 seconds
INFO:root:Cycle: 0, forward NEQ step: 1500, took: 0.020230770111083984 seconds
INFO:root:Cycle: 0, forward NEQ step: 2250, took: 0.02013707160949707 seconds
INFO:root:Cycle: 0, forward

Try to optimize performance -- change ewaldTolerance

In [1]:
import logging
import pickle
import numpy as np
from openmmtools.integrators import PeriodicNonequilibriumIntegrator
from simtk import unit
from simtk import openmm
import argparse
import os
import time
import mdtraj as md
from simtk.openmm import XmlSerializer

In [2]:
# Set up logger
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

# Define lambda functions
x = 'lambda'
DEFAULT_ALCHEMICAL_FUNCTIONS = {
                             'lambda_sterics_core': x,
                             'lambda_electrostatics_core': x,
                             'lambda_sterics_insert': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_sterics_delete': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_insert': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_delete': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_bonds': x,
                             'lambda_angles': x,
                             'lambda_torsions': x}

# Define simulation parameters
# nsteps_eq = 250000 # 1 ns
# nsteps_neq = 250000 # 1 ns
nsteps_eq = 2500 # 10 ps
nsteps_neq = 2500 # 10 ps
neq_splitting='V R H O R V'
timestep = 4.0 * unit.femtosecond
platform_name = 'CUDA'

In [3]:
# Read in htf
with open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN12/htf.npz", 'rb') as f:
    htf = np.load(f, allow_pickle=True)
    htf = htf.get('arr_0')
    htf = htf.flatten()[0]
# system = htf.hybrid_system
# positions = htf.hybrid_positions


DEBUG:numba.core.byteflow:bytecode dump:
>          0	NOP(arg=None, lineno=6)
           2	LOAD_GLOBAL(arg=0, lineno=6)
           4	LOAD_METHOD(arg=1, lineno=6)
           6	LOAD_CONST(arg=1, lineno=6)
           8	CALL_METHOD(arg=1, lineno=6)
          10	STORE_FAST(arg=2, lineno=6)
          12	LOAD_FAST(arg=0, lineno=7)
          14	LOAD_CONST(arg=2, lineno=7)
          16	BINARY_SUBSCR(arg=None, lineno=7)
          18	LOAD_FAST(arg=1, lineno=7)
          20	LOAD_CONST(arg=3, lineno=7)
          22	BINARY_SUBSCR(arg=None, lineno=7)
          24	BINARY_MULTIPLY(arg=None, lineno=7)
          26	LOAD_FAST(arg=0, lineno=7)
          28	LOAD_CONST(arg=3, lineno=7)
          30	BINARY_SUBSCR(arg=None, lineno=7)
          32	LOAD_FAST(arg=1, lineno=7)
          34	LOAD_CONST(arg=2, lineno=7)
          36	BINARY_SUBSCR(arg=None, lineno=7)
          38	BINARY_MULTIPLY(arg=None, lineno=7)
          40	BINARY_SUBTRACT(arg=None, lineno=7)
          42	LOAD_FAST(arg=2, lineno=7)
          44	LO

DEBUG:numba.core.byteflow:dispatch pc=74, inst=BINARY_MULTIPLY(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$66binary_subscr.30', '$72binary_subscr.33']
DEBUG:numba.core.byteflow:dispatch pc=76, inst=BINARY_SUBTRACT(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$74binary_multiply.34']
DEBUG:numba.core.byteflow:dispatch pc=78, inst=LOAD_FAST(arg=2, lineno=8)
DEBUG:numba.core.byteflow:stack ['$76binary_subtract.35']
DEBUG:numba.core.byteflow:dispatch pc=80, inst=LOAD_CONST(arg=2, lineno=8)
DEBUG:numba.core.byteflow:stack ['$76binary_subtract.35', '$c78.36']
DEBUG:numba.core.byteflow:dispatch pc=82, inst=STORE_SUBSCR(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$76binary_subtract.35', '$c78.36', '$const80.37']
DEBUG:numba.core.byteflow:dispatch pc=84, inst=LOAD_FAST(arg=0, lineno=9)
DEBUG:numba.core.byteflow:stack []
DEBUG:numba.core.byteflow:dispatch pc=86, inst=LOAD_CONST(arg=4, lineno=9)
DEBUG:numba.core.bytefl

DEBUG:numba.core.ssa:-----------------------------------BEFORE SSA-----------------------------------
DEBUG:numba.core.ssa:label 0:
    a = arg(0, name=a)                       ['a']
    b = arg(1, name=b)                       ['b']
    $2load_global.0 = global(np: <module 'numpy' from '/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/numpy/__init__.py'>) ['$2load_global.0']
    $4load_method.1 = getattr(value=$2load_global.0, attr=zeros) ['$2load_global.0', '$4load_method.1']
    $const6.2 = const(int, 3)                ['$const6.2']
    $8call_method.3 = call $4load_method.1($const6.2, func=$4load_method.1, args=[Var($const6.2, coordinate_numba.py:6)], kws=(), vararg=None) ['$4load_method.1', '$8call_method.3', '$const6.2']
    c = $8call_method.3                      ['$8call_method.3', 'c']
    $const14.5 = const(int, 1)               ['$const14.5']
    $16binary_subscr.6 = static_getitem(value=a, index=1, index_var=$const14.5) ['$16binary_subscr.6', '$const14.

DEBUG:numba.core.ssa:on stmt: $94binary_subscr.43 = static_getitem(value=b, index=1, index_var=$const92.42)
DEBUG:numba.core.ssa:on stmt: $96binary_multiply.44 = $88binary_subscr.40 * $94binary_subscr.43
DEBUG:numba.core.ssa:on stmt: $const100.46 = const(int, 1)
DEBUG:numba.core.ssa:on stmt: $102binary_subscr.47 = static_getitem(value=a, index=1, index_var=$const100.46)
DEBUG:numba.core.ssa:on stmt: $const106.49 = const(int, 0)
DEBUG:numba.core.ssa:on stmt: $108binary_subscr.50 = static_getitem(value=b, index=0, index_var=$const106.49)
DEBUG:numba.core.ssa:on stmt: $110binary_multiply.51 = $102binary_subscr.47 * $108binary_subscr.50
DEBUG:numba.core.ssa:on stmt: $112binary_subtract.52 = $96binary_multiply.44 - $110binary_multiply.51
DEBUG:numba.core.ssa:on stmt: $const116.54 = const(int, 2)
DEBUG:numba.core.ssa:on stmt: c[2] = $112binary_subtract.52
DEBUG:numba.core.ssa:on stmt: $122return_value.56 = cast(value=c)
DEBUG:numba.core.ssa:on stmt: return $122return_value.56
DEBUG:numba.cor

DEBUG:numba.core.ssa:================================================================================
DEBUG:numba.core.byteflow:bytecode dump:
>          0	NOP(arg=None, lineno=14)
           2	LOAD_GLOBAL(arg=0, lineno=14)
           4	LOAD_METHOD(arg=1, lineno=14)
           6	LOAD_FAST(arg=0, lineno=14)
           8	LOAD_FAST(arg=0, lineno=14)
          10	CALL_METHOD(arg=2, lineno=14)
          12	STORE_FAST(arg=1, lineno=14)
          14	LOAD_GLOBAL(arg=0, lineno=15)
          16	LOAD_METHOD(arg=2, lineno=15)
          18	LOAD_FAST(arg=1, lineno=15)
          20	CALL_METHOD(arg=1, lineno=15)
          22	RETURN_VALUE(arg=None, lineno=15)
DEBUG:numba.core.byteflow:pending: deque([State(pc_initial=0 nstack_initial=0)])
DEBUG:numba.core.byteflow:stack: []
DEBUG:numba.core.byteflow:dispatch pc=0, inst=NOP(arg=None, lineno=14)
DEBUG:numba.core.byteflow:stack []
DEBUG:numba.core.byteflow:dispatch pc=2, inst=LOAD_GLOBAL(arg=0, lineno=14)
DEBUG:numba.core.byteflow:stack []
DEBUG:numba.cor

...

DEBUG:numba.core.ssa:==== SSA block rewrite pass on 174
DEBUG:numba.core.ssa:Running <numba.core.ssa._FixSSAVars object at 0x2b469ce9cd30>
DEBUG:numba.core.ssa:on stmt: $const174.0 = const(float, -1.0)
DEBUG:numba.core.ssa:on stmt: cos_phi.1 = $const174.0
DEBUG:numba.core.ssa:on stmt: jump 192
DEBUG:numba.core.ssa:==== SSA block rewrite pass on 180
DEBUG:numba.core.ssa:Running <numba.core.ssa._FixSSAVars object at 0x2b469ce9cd30>
DEBUG:numba.core.ssa:on stmt: $const182.1 = const(float, 1.0)
DEBUG:numba.core.ssa:on stmt: $184compare_op.2 = cos_phi > $const182.1
DEBUG:numba.core.ssa:on stmt: branch $184compare_op.2, 188, 192
DEBUG:numba.core.ssa:==== SSA block rewrite pass on 188
DEBUG:numba.core.ssa:Running <numba.core.ssa._FixSSAVars object at 0x2b469ce9cd30>
DEBUG:numba.core.ssa:on stmt: $const188.0 = const(float, 1.0)
DEBUG:numba.core.ssa:on stmt: cos_phi.2 = $const188.0
DEBUG:numba.core.ssa:on stmt: jump 192
DEBUG:numba.core.ssa:==== SSA block rewrite pass on 192
DEBUG:numba.core.ss

DEBUG:numba.core.ssa:================================================================================
/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/perses-0.7.1-py3.7.egg/perses/rjmc/coordinate_numba.py:129: NumbaPerformanceWarning: np.dot() is faster on contiguous arrays, called on (array(float64, 1d, A), array(float64, 1d, A))
  cos_phi = np.dot(plane1, plane2) / (_norm(plane1)*_norm(plane2))
/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/perses-0.7.1-py3.7.egg/perses/rjmc/coordinate_numba.py:137: NumbaPerformanceWarning: np.dot() is faster on contiguous arrays, called on (array(float64, 1d, C), array(float64, 1d, A))
  if np.dot(a, plane2) <= 0:
DEBUG:numba.core.byteflow:bytecode dump:
>          0	NOP(arg=None, lineno=106)
           2	LOAD_FAST(arg=0, lineno=106)
           4	LOAD_FAST(arg=1, lineno=106)
           6	BINARY_SUBTRACT(arg=None, lineno=106)
           8	RETURN_VALUE(arg=None, lineno=106)
DEBUG:numba.core.byteflow:pending: 

DEBUG:numba.core.ssa:================================================================================
DEBUG:numba.core.ssa:==== SSA block analysis pass on 0
DEBUG:numba.core.ssa:Running <numba.core.ssa._GatherDefsHandler object at 0x2b469cc1a710>
DEBUG:numba.core.ssa:on stmt: angle_position_1 = arg(0, name=angle_position_1)
DEBUG:numba.core.ssa:on stmt: bond_position_2 = arg(1, name=bond_position_2)
DEBUG:numba.core.ssa:on stmt: $6binary_subtract.2 = angle_position_1 - bond_position_2
DEBUG:numba.core.ssa:on stmt: $8return_value.3 = cast(value=$6binary_subtract.2)
DEBUG:numba.core.ssa:on stmt: return $8return_value.3
DEBUG:numba.core.ssa:defs defaultdict(<class 'list'>,
            {'$6binary_subtract.2': [<numba.core.ir.Assign object at 0x2b469cc5e588>],
             '$8return_value.3': [<numba.core.ir.Assign object at 0x2b469cc5e518>],
             'angle_position_1': [<numba.core.ir.Assign object at 0x2b469cc5e278>],
             'bond_position_2': [<numba.core.ir.Assign object at 0

DEBUG:numba.core.byteflow:----------------------DONE Prune PHIs-----------------------
DEBUG:numba.core.byteflow:block_infos State(pc_initial=0 nstack_initial=0):
AdaptBlockInfo(insts=((0, {}), (2, {'res': '$a_12.0'}), (4, {'res': '$_32call_function_12_14.1'}), (6, {'lhs': '$a_12.0', 'rhs': '$_32call_function_12_14.1', 'res': '$6binary_true_divide.2'}), (8, {'retval': '$6binary_true_divide.2', 'castval': '$8return_value.3'})), outgoing_phis={}, blockstack=(), active_try_block=None, outgoing_edgepushed={})
DEBUG:numba.core.interpreter:label 0:
    _32call_function_12_1 = arg(0, name=_32call_function_12_1) ['_32call_function_12_1']
    a_1 = arg(1, name=a_1)                   ['a_1']
    $6binary_true_divide.2 = a_1 / _32call_function_12_1 ['$6binary_true_divide.2', '_32call_function_12_1', 'a_1']
    $8return_value.3 = cast(value=$6binary_true_divide.2) ['$6binary_true_divide.2', '$8return_value.3']
    return $8return_value.3                  ['$8return_value.3']

DEBUG:numba.core.ssa:

DEBUG:numba.core.byteflow:pending: deque([State(pc_initial=0 nstack_initial=0)])
DEBUG:numba.core.byteflow:stack: []
DEBUG:numba.core.byteflow:dispatch pc=0, inst=NOP(arg=None, lineno=109)
DEBUG:numba.core.byteflow:stack []
DEBUG:numba.core.byteflow:dispatch pc=2, inst=LOAD_FAST(arg=1, lineno=109)
DEBUG:numba.core.byteflow:stack []
DEBUG:numba.core.byteflow:dispatch pc=4, inst=LOAD_FAST(arg=0, lineno=112)
DEBUG:numba.core.byteflow:stack ['$c_12.0']
DEBUG:numba.core.byteflow:dispatch pc=6, inst=BINARY_TRUE_DIVIDE(arg=None, lineno=112)
DEBUG:numba.core.byteflow:stack ['$c_12.0', '$_56call_function_22_14.1']
DEBUG:numba.core.byteflow:dispatch pc=8, inst=RETURN_VALUE(arg=None, lineno=112)
DEBUG:numba.core.byteflow:stack ['$6binary_true_divide.2']
DEBUG:numba.core.byteflow:end state. edges=[]
DEBUG:numba.core.byteflow:-------------------------Prune PHIs-------------------------
DEBUG:numba.core.byteflow:Used_phis: defaultdict(<class 'set'>, {State(pc_initial=0 nstack_initial=0): set()})
DEB

In [7]:
htf

In [13]:
# Make integrator
from openmmtools.integrators import PeriodicNonequilibriumIntegrator
integrator = PeriodicNonequilibriumIntegrator(DEFAULT_ALCHEMICAL_FUNCTIONS, nsteps_eq, nsteps_neq, neq_splitting, timestep=timestep)

In [14]:
integrator.setConstraintTolerance(1e-6)

In [15]:
# Deserialize system file 
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN12/system.xml.bz2", 'rb') as f:
    system = XmlSerializer.deserialize(f.read().decode("utf-8"))


In [16]:
# Set up context
platform_name = 'OpenCL'
platform = openmm.Platform.getPlatformByName(platform_name)
if platform_name in ['CUDA', 'OpenCL']:
    platform.setPropertyDefaultValue('Precision', 'mixed')
if platform_name in ['CUDA']:
    platform.setPropertyDefaultValue('DeterministicForces', 'true')
context = openmm.Context(system, integrator, platform)


In [17]:
# Load state and set box vectors, positions, and velocities
import bz2
with bz2.open("/data/chodera/zhangi/perses_benchmark/fah/17300/RUNS/RUN12/state.xml.bz2", 'rb') as infile:
    state = XmlSerializer.deserialize(infile.read().decode('utf-8'))
context.setPeriodicBoxVectors(*state.getPeriodicBoxVectors())
context.setPositions(state.getPositions())
context.setVelocities(state.getVelocities())


In [18]:
# Run neq
phase = 'complex'
i = 17300
ncycles = 1
forward_works_master, reverse_works_master = list(), list()
forward_eq_old, forward_neq_old, forward_neq_new = list(), list(), list()
reverse_eq_new, reverse_neq_old, reverse_neq_new = list(), list(), list()
for cycle in range(ncycles):
    # Equilibrium (lambda = 0)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 0, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            forward_eq_old.append(old_pos)

    # Forward (0 -> 1)
    forward_works = [integrator.get_protocol_work(dimensionless=True)]
    for fwd_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        forward_works.append(integrator.get_protocol_work(dimensionless=True))
        if fwd_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, forward NEQ step: {fwd_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            forward_neq_old.append(old_pos)
            forward_neq_new.append(new_pos)
    forward_works_master.append(forward_works)
    
    # Equilibrium (lambda = 1)
    for step in range(nsteps_eq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        if step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, Step: {step}, equilibrating at lambda = 1, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_eq_new.append(new_pos)

    # Reverse work (1 -> 0)
    reverse_works = [integrator.get_protocol_work(dimensionless=True)]
    for rev_step in range(nsteps_neq):
        initial_time = time.time()
        integrator.step(1)
        elapsed_time = (time.time() - initial_time) * unit.seconds
        reverse_works.append(integrator.get_protocol_work(dimensionless=True))
        if rev_step % 750 == 0:
            _logger.info(f'Cycle: {cycle}, reverse NEQ step: {rev_step}, took: {elapsed_time / unit.seconds} seconds')
            pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
            old_pos = np.asarray(htf.old_positions(pos))
            new_pos = np.asarray(htf.new_positions(pos))
            reverse_neq_old.append(old_pos)
            reverse_neq_new.append(new_pos)
    reverse_works_master.append(reverse_works)
        
#     # Save works
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward.npy"), 'wb') as f:
#         np.save(f, forward_works_master)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse.npy"), 'wb') as f:
#         np.save(f, reverse_works_master)

#     # Save trajs
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_eq_old.npy"), 'wb') as f:
#         np.save(f, forward_eq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_eq_new.npy"), 'wb') as f:
#         np.save(f, reverse_eq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_old.npy"), 'wb') as f:
#         np.save(f, forward_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_forward_neq_new.npy"), 'wb') as f:
#         np.save(f, forward_neq_new)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_old.npy"), 'wb') as f:
#         np.save(f, reverse_neq_old)
#     with open(os.path.join(args.dir, f"{i}_{phase}_reverse_neq_new.npy"), 'wb') as f:
#         np.save(f, reverse_neq_new)



INFO:root:Cycle: 0, Step: 0, equilibrating at lambda = 0, took: 0.04516410827636719 seconds
INFO:root:Cycle: 0, Step: 750, equilibrating at lambda = 0, took: 0.008925914764404297 seconds
INFO:root:Cycle: 0, Step: 1500, equilibrating at lambda = 0, took: 0.008986473083496094 seconds
INFO:root:Cycle: 0, Step: 2250, equilibrating at lambda = 0, took: 0.00910186767578125 seconds
INFO:root:Cycle: 0, forward NEQ step: 0, took: 0.008863687515258789 seconds
INFO:root:Cycle: 0, forward NEQ step: 750, took: 0.009029388427734375 seconds
INFO:root:Cycle: 0, forward NEQ step: 1500, took: 0.009085416793823242 seconds
INFO:root:Cycle: 0, forward NEQ step: 2250, took: 0.009061813354492188 seconds
INFO:root:Cycle: 0, Step: 0, equilibrating at lambda = 1, took: 0.008899211883544922 seconds
INFO:root:Cycle: 0, Step: 750, equilibrating at lambda = 1, took: 0.008941411972045898 seconds
INFO:root:Cycle: 0, Step: 1500, equilibrating at lambda = 1, took: 0.009001731872558594 seconds
INFO:root:Cycle: 0, Step: 

In [75]:
for i in range(htf.hybrid_system.getNumConstraints()):
    print(htf.hybrid_system.getConstraintParameters(i))

[1441, 1442, Quantity(value=0.09572, unit=nanometer)]
[1441, 1443, Quantity(value=0.09572, unit=nanometer)]
[3153, 3154, Quantity(value=0.09572, unit=nanometer)]
[3153, 3155, Quantity(value=0.09572, unit=nanometer)]
[3156, 3157, Quantity(value=0.09572, unit=nanometer)]
[3156, 3158, Quantity(value=0.09572, unit=nanometer)]
[3159, 3160, Quantity(value=0.09572, unit=nanometer)]
[3159, 3161, Quantity(value=0.09572, unit=nanometer)]
[3162, 3163, Quantity(value=0.09572, unit=nanometer)]
[3162, 3164, Quantity(value=0.09572, unit=nanometer)]
[3165, 3166, Quantity(value=0.09572, unit=nanometer)]
[3165, 3167, Quantity(value=0.09572, unit=nanometer)]
[3168, 3169, Quantity(value=0.09572, unit=nanometer)]
[3168, 3170, Quantity(value=0.09572, unit=nanometer)]
[3171, 3172, Quantity(value=0.09572, unit=nanometer)]
[3171, 3173, Quantity(value=0.09572, unit=nanometer)]
[3174, 3175, Quantity(value=0.09572, unit=nanometer)]
[3174, 3176, Quantity(value=0.09572, unit=nanometer)]
[3177, 3178, Quantity(value=

[8073, 8074, Quantity(value=0.09572, unit=nanometer)]
[8073, 8075, Quantity(value=0.09572, unit=nanometer)]
[8076, 8077, Quantity(value=0.09572, unit=nanometer)]
[8076, 8078, Quantity(value=0.09572, unit=nanometer)]
[8079, 8080, Quantity(value=0.09572, unit=nanometer)]
[8079, 8081, Quantity(value=0.09572, unit=nanometer)]
[8082, 8083, Quantity(value=0.09572, unit=nanometer)]
[8082, 8084, Quantity(value=0.09572, unit=nanometer)]
[8085, 8086, Quantity(value=0.09572, unit=nanometer)]
[8085, 8087, Quantity(value=0.09572, unit=nanometer)]
[8088, 8089, Quantity(value=0.09572, unit=nanometer)]
[8088, 8090, Quantity(value=0.09572, unit=nanometer)]
[8091, 8092, Quantity(value=0.09572, unit=nanometer)]
[8091, 8093, Quantity(value=0.09572, unit=nanometer)]
[8094, 8095, Quantity(value=0.09572, unit=nanometer)]
[8094, 8096, Quantity(value=0.09572, unit=nanometer)]
[8097, 8098, Quantity(value=0.09572, unit=nanometer)]
[8097, 8099, Quantity(value=0.09572, unit=nanometer)]
[8100, 8101, Quantity(value=

[13320, 13322, Quantity(value=0.09572, unit=nanometer)]
[13323, 13324, Quantity(value=0.09572, unit=nanometer)]
[13323, 13325, Quantity(value=0.09572, unit=nanometer)]
[13326, 13327, Quantity(value=0.09572, unit=nanometer)]
[13326, 13328, Quantity(value=0.09572, unit=nanometer)]
[13329, 13330, Quantity(value=0.09572, unit=nanometer)]
[13329, 13331, Quantity(value=0.09572, unit=nanometer)]
[13332, 13333, Quantity(value=0.09572, unit=nanometer)]
[13332, 13334, Quantity(value=0.09572, unit=nanometer)]
[13335, 13336, Quantity(value=0.09572, unit=nanometer)]
[13335, 13337, Quantity(value=0.09572, unit=nanometer)]
[13338, 13339, Quantity(value=0.09572, unit=nanometer)]
[13338, 13340, Quantity(value=0.09572, unit=nanometer)]
[13341, 13342, Quantity(value=0.09572, unit=nanometer)]
[13341, 13343, Quantity(value=0.09572, unit=nanometer)]
[13344, 13345, Quantity(value=0.09572, unit=nanometer)]
[13344, 13346, Quantity(value=0.09572, unit=nanometer)]
[13347, 13348, Quantity(value=0.09572, unit=nano

[19320, 19322, Quantity(value=0.09572, unit=nanometer)]
[19323, 19324, Quantity(value=0.09572, unit=nanometer)]
[19323, 19325, Quantity(value=0.09572, unit=nanometer)]
[19326, 19327, Quantity(value=0.09572, unit=nanometer)]
[19326, 19328, Quantity(value=0.09572, unit=nanometer)]
[19329, 19330, Quantity(value=0.09572, unit=nanometer)]
[19329, 19331, Quantity(value=0.09572, unit=nanometer)]
[19332, 19333, Quantity(value=0.09572, unit=nanometer)]
[19332, 19334, Quantity(value=0.09572, unit=nanometer)]
[19335, 19336, Quantity(value=0.09572, unit=nanometer)]
[19335, 19337, Quantity(value=0.09572, unit=nanometer)]
[19338, 19339, Quantity(value=0.09572, unit=nanometer)]
[19338, 19340, Quantity(value=0.09572, unit=nanometer)]
[19341, 19342, Quantity(value=0.09572, unit=nanometer)]
[19341, 19343, Quantity(value=0.09572, unit=nanometer)]
[19344, 19345, Quantity(value=0.09572, unit=nanometer)]
[19344, 19346, Quantity(value=0.09572, unit=nanometer)]
[19347, 19348, Quantity(value=0.09572, unit=nano

[25320, 25321, Quantity(value=0.09572, unit=nanometer)]
[25320, 25322, Quantity(value=0.09572, unit=nanometer)]
[25323, 25324, Quantity(value=0.09572, unit=nanometer)]
[25323, 25325, Quantity(value=0.09572, unit=nanometer)]
[25326, 25327, Quantity(value=0.09572, unit=nanometer)]
[25326, 25328, Quantity(value=0.09572, unit=nanometer)]
[25329, 25330, Quantity(value=0.09572, unit=nanometer)]
[25329, 25331, Quantity(value=0.09572, unit=nanometer)]
[25332, 25333, Quantity(value=0.09572, unit=nanometer)]
[25332, 25334, Quantity(value=0.09572, unit=nanometer)]
[25335, 25336, Quantity(value=0.09572, unit=nanometer)]
[25335, 25337, Quantity(value=0.09572, unit=nanometer)]
[25338, 25339, Quantity(value=0.09572, unit=nanometer)]
[25338, 25340, Quantity(value=0.09572, unit=nanometer)]
[25341, 25342, Quantity(value=0.09572, unit=nanometer)]
[25341, 25343, Quantity(value=0.09572, unit=nanometer)]
[25344, 25345, Quantity(value=0.09572, unit=nanometer)]
[25344, 25346, Quantity(value=0.09572, unit=nano

...

[60567, 60568, Quantity(value=0.09572, unit=nanometer)]
[60567, 60569, Quantity(value=0.09572, unit=nanometer)]
[60570, 60571, Quantity(value=0.09572, unit=nanometer)]
[60570, 60572, Quantity(value=0.09572, unit=nanometer)]
[60573, 60574, Quantity(value=0.09572, unit=nanometer)]
[60573, 60575, Quantity(value=0.09572, unit=nanometer)]
[60576, 60577, Quantity(value=0.09572, unit=nanometer)]
[60576, 60578, Quantity(value=0.09572, unit=nanometer)]
[60579, 60580, Quantity(value=0.09572, unit=nanometer)]
[60579, 60581, Quantity(value=0.09572, unit=nanometer)]
[60582, 60583, Quantity(value=0.09572, unit=nanometer)]
[60582, 60584, Quantity(value=0.09572, unit=nanometer)]
[60585, 60586, Quantity(value=0.09572, unit=nanometer)]
[60585, 60587, Quantity(value=0.09572, unit=nanometer)]
[60588, 60589, Quantity(value=0.09572, unit=nanometer)]
[60588, 60590, Quantity(value=0.09572, unit=nanometer)]
[60591, 60592, Quantity(value=0.09572, unit=nanometer)]
[60591, 60593, Quantity(value=0.09572, unit=nano

[68064, 68066, Quantity(value=0.09572, unit=nanometer)]
[68067, 68068, Quantity(value=0.09572, unit=nanometer)]
[68067, 68069, Quantity(value=0.09572, unit=nanometer)]
[68070, 68071, Quantity(value=0.09572, unit=nanometer)]
[68070, 68072, Quantity(value=0.09572, unit=nanometer)]
[68073, 68074, Quantity(value=0.09572, unit=nanometer)]
[68073, 68075, Quantity(value=0.09572, unit=nanometer)]
[68076, 68077, Quantity(value=0.09572, unit=nanometer)]
[68076, 68078, Quantity(value=0.09572, unit=nanometer)]
[68079, 68080, Quantity(value=0.09572, unit=nanometer)]
[68079, 68081, Quantity(value=0.09572, unit=nanometer)]
[68082, 68083, Quantity(value=0.09572, unit=nanometer)]
[68082, 68084, Quantity(value=0.09572, unit=nanometer)]
[68085, 68086, Quantity(value=0.09572, unit=nanometer)]
[68085, 68087, Quantity(value=0.09572, unit=nanometer)]
[68088, 68089, Quantity(value=0.09572, unit=nanometer)]
[68088, 68090, Quantity(value=0.09572, unit=nanometer)]
[68091, 68092, Quantity(value=0.09572, unit=nano

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[62527, 62528, Quantity(value=0.15139006545247014, unit=nanometer)]
[62530, 62531, Quantity(value=0.15139006545247014, unit=nanometer)]
[62533, 62534, Quantity(value=0.15139006545247014, unit=nanometer)]
[62536, 62537, Quantity(value=0.15139006545247014, unit=nanometer)]
[62539, 62540, Quantity(value=0.15139006545247014, unit=nanometer)]
[62542, 62543, Quantity(value=0.15139006545247014, unit=nanometer)]
[62545, 62546, Quantity(value=0.15139006545247014, unit=nanometer)]
[62548, 62549, Quantity(value=0.15139006545247014, unit=nanometer)]
[62551, 62552, Quantity(value=0.15139006545247014, unit=nanometer)]
[62554, 62555, Quantity(value=0.15139006545247014, unit=nanometer)]
[62557, 62558, Quantity(value=0.15139006545247014, unit=nanometer)]
[62560, 62561, Quantity(value=0.15139006545247014, unit=nanometer)]
[62563, 62564, Quantity(value=0.15139006545247014, unit=nanometer)]
[62566, 62567, Quantity(value=0.15139006545247014, unit=nanometer)]
[62569, 62570, Quantity(value=0.1513900654524701

[77524, 77525, Quantity(value=0.15139006545247014, unit=nanometer)]
[77527, 77528, Quantity(value=0.15139006545247014, unit=nanometer)]
[77530, 77531, Quantity(value=0.15139006545247014, unit=nanometer)]
[77533, 77534, Quantity(value=0.15139006545247014, unit=nanometer)]
[77536, 77537, Quantity(value=0.15139006545247014, unit=nanometer)]
[77539, 77540, Quantity(value=0.15139006545247014, unit=nanometer)]
[77542, 77543, Quantity(value=0.15139006545247014, unit=nanometer)]
[77545, 77546, Quantity(value=0.15139006545247014, unit=nanometer)]
[77548, 77549, Quantity(value=0.15139006545247014, unit=nanometer)]
[77551, 77552, Quantity(value=0.15139006545247014, unit=nanometer)]
[77554, 77555, Quantity(value=0.15139006545247014, unit=nanometer)]
[77557, 77558, Quantity(value=0.15139006545247014, unit=nanometer)]
[77560, 77561, Quantity(value=0.15139006545247014, unit=nanometer)]
[77563, 77564, Quantity(value=0.15139006545247014, unit=nanometer)]
[77566, 77567, Quantity(value=0.1513900654524701

In [78]:
for atom in htf.hybrid_topology.atoms:
    print(atom, atom.index)

ACE0-CH3 0
ACE0-C 1
ACE0-O 2
ACE0-H1 3
ACE0-H2 4
ACE0-H3 5
LYS1-N 6
LYS1-CA 7
LYS1-C 8
LYS1-O 9
LYS1-CB 10
LYS1-CG 11
LYS1-CD 12
LYS1-CE 13
LYS1-NZ 14
LYS1-H2 15
LYS1-HA 16
LYS1-HB3 17
LYS1-HB2 18
LYS1-HG2 19
LYS1-HG3 20
LYS1-HD2 21
LYS1-HD3 22
LYS1-HE3 23
LYS1-HE2 24
LYS1-HZ1 25
LYS1-HZ2 26
LYS1-HZ3 27
LYS2-N 28
LYS2-CA 29
LYS2-C 30
LYS2-O 31
LYS2-CB 32
LYS2-CG 33
LYS2-CD 34
LYS2-CE 35
LYS2-NZ 36
LYS2-H 37
LYS2-HA 38
LYS2-HB3 39
LYS2-HB2 40
LYS2-HG2 41
LYS2-HG3 42
LYS2-HD3 43
LYS2-HD2 44
LYS2-HE3 45
LYS2-HE2 46
LYS2-HZ1 47
LYS2-HZ2 48
LYS2-HZ3 49
ALA3-N 50
ALA3-CA 51
ALA3-C 52
ALA3-O 53
ALA3-CB 54
ALA3-H 55
ALA3-HA 56
ALA3-HB1 57
ALA3-HB2 58
ALA3-HB3 59
VAL4-N 60
VAL4-CA 61
VAL4-C 62
VAL4-O 63
VAL4-CB 64
VAL4-CG1 65
VAL4-CG2 66
VAL4-H 67
VAL4-HA 68
VAL4-HB 69
VAL4-HG11 70
VAL4-HG12 71
VAL4-HG13 72
VAL4-HG21 73
VAL4-HG22 74
VAL4-HG23 75
ILE5-N 76
ILE5-CA 77
ILE5-C 78
ILE5-O 79
ILE5-CB 80
ILE5-CG1 81
ILE5-CG2 82
ILE5-CD1 83
ILE5-H 84
ILE5-HA 85
ILE5-HB 86
ILE5-HG13 87
ILE5-HG12 88
ILE5-

ILE4-O 1469
ILE4-CB 1470
ILE4-CG1 1471
ILE4-CG2 1472
ILE4-CD1 1473
ILE4-H 1474
ILE4-HA 1475
ILE4-HB 1476
ILE4-HG13 1477
ILE4-HG12 1478
ILE4-HG21 1479
ILE4-HG22 1480
ILE4-HG23 1481
ILE4-HD11 1482
ILE4-HD12 1483
ILE4-HD13 1484
ASN5-N 1485
ASN5-CA 1486
ASN5-C 1487
ASN5-O 1488
ASN5-CB 1489
ASN5-CG 1490
ASN5-OD1 1491
ASN5-ND2 1492
ASN5-H 1493
ASN5-HA 1494
ASN5-HB2 1495
ASN5-HB3 1496
ASN5-HD21 1497
ASN5-HD22 1498
THR6-N 1499
THR6-CA 1500
THR6-C 1501
THR6-O 1502
THR6-CB 1503
THR6-OG1 1504
THR6-CG2 1505
THR6-H 1506
THR6-HA 1507
THR6-HB 1508
THR6-HG1 1509
THR6-HG21 1510
THR6-HG22 1511
THR6-HG23 1512
PHE7-N 1513
PHE7-CA 1514
PHE7-C 1515
PHE7-O 1516
PHE7-CB 1517
PHE7-CG 1518
PHE7-CD1 1519
PHE7-CD2 1520
PHE7-CE1 1521
PHE7-CE2 1522
PHE7-CZ 1523
PHE7-H 1524
PHE7-HA 1525
PHE7-HB3 1526
PHE7-HB2 1527
PHE7-HD1 1528
PHE7-HD2 1529
PHE7-HE1 1530
PHE7-HE2 1531
PHE7-HZ 1532
ASP8-N 1533
ASP8-CA 1534
ASP8-C 1535
ASP8-O 1536
ASP8-CB 1537
ASP8-CG 1538
ASP8-OD1 1539
ASP8-OD2 1540
ASP8-H 1541
ASP8-HA 1542
ASP8-HB3

ASP101-C 2969
ASP101-O 2970
ASP101-CB 2971
ASP101-CG 2972
ASP101-OD1 2973
ASP101-OD2 2974
ASP101-H 2975
ASP101-HA 2976
ASP101-HB2 2977
ASP101-HB3 2978
HIS102-N 2979
HIS102-CA 2980
HIS102-C 2981
HIS102-O 2982
HIS102-CB 2983
HIS102-CG 2984
HIS102-ND1 2985
HIS102-CD2 2986
HIS102-CE1 2987
HIS102-NE2 2988
HIS102-H 2989
HIS102-HA 2990
HIS102-HB3 2991
HIS102-HB2 2992
HIS102-HD2 2993
HIS102-HE1 2994
HIS102-HE2 2995
TYR103-N 2996
TYR103-CA 2997
TYR103-C 2998
TYR103-O 2999
TYR103-CB 3000
TYR103-CG 3001
TYR103-CD1 3002
TYR103-CD2 3003
TYR103-CE1 3004
TYR103-CE2 3005
TYR103-CZ 3006
TYR103-OH 3007
TYR103-H 3008
TYR103-HA 3009
TYR103-HB2 3010
TYR103-HB3 3011
TYR103-HD1 3012
TYR103-HD2 3013
TYR103-HE1 3014
TYR103-HE2 3015
TYR103-HH 3016
GLN104-N 3017
GLN104-CA 3018
GLN104-C 3019
GLN104-O 3020
GLN104-CB 3021
GLN104-CG 3022
GLN104-CD 3023
GLN104-OE1 3024
GLN104-NE2 3025
GLN104-H 3026
GLN104-HA 3027
GLN104-HB3 3028
GLN104-HB2 3029
GLN104-HG3 3030
GLN104-HG2 3031
GLN104-HE21 3032
GLN104-HE22 3033
THR105-

HOH811-H1 4969
HOH811-H2 4970
HOH812-O 4971
HOH812-H1 4972
HOH812-H2 4973
HOH813-O 4974
HOH813-H1 4975
HOH813-H2 4976
HOH814-O 4977
HOH814-H1 4978
HOH814-H2 4979
HOH815-O 4980
HOH815-H1 4981
HOH815-H2 4982
HOH816-O 4983
HOH816-H1 4984
HOH816-H2 4985
HOH817-O 4986
HOH817-H1 4987
HOH817-H2 4988
HOH818-O 4989
HOH818-H1 4990
HOH818-H2 4991
HOH819-O 4992
HOH819-H1 4993
HOH819-H2 4994
HOH820-O 4995
HOH820-H1 4996
HOH820-H2 4997
HOH821-O 4998
HOH821-H1 4999
HOH821-H2 5000
HOH822-O 5001
HOH822-H1 5002
HOH822-H2 5003
HOH823-O 5004
HOH823-H1 5005
HOH823-H2 5006
HOH824-O 5007
HOH824-H1 5008
HOH824-H2 5009
HOH825-O 5010
HOH825-H1 5011
HOH825-H2 5012
HOH826-O 5013
HOH826-H1 5014
HOH826-H2 5015
HOH827-O 5016
HOH827-H1 5017
HOH827-H2 5018
HOH828-O 5019
HOH828-H1 5020
HOH828-H2 5021
HOH829-O 5022
HOH829-H1 5023
HOH829-H2 5024
HOH830-O 5025
HOH830-H1 5026
HOH830-H2 5027
HOH831-O 5028
HOH831-H1 5029
HOH831-H2 5030
HOH832-O 5031
HOH832-H1 5032
HOH832-H2 5033
HOH833-O 5034
HOH833-H1 5035
HOH833-H2 5036
HO

HOH1400-H1 6718
HOH1400-H2 6719
HOH1401-O 6720
HOH1401-H1 6721
HOH1401-H2 6722
HOH1402-O 6723
HOH1402-H1 6724
HOH1402-H2 6725
HOH1403-O 6726
HOH1403-H1 6727
HOH1403-H2 6728
HOH1404-O 6729
HOH1404-H1 6730
HOH1404-H2 6731
HOH1405-O 6732
HOH1405-H1 6733
HOH1405-H2 6734
HOH1406-O 6735
HOH1406-H1 6736
HOH1406-H2 6737
HOH1407-O 6738
HOH1407-H1 6739
HOH1407-H2 6740
HOH1408-O 6741
HOH1408-H1 6742
HOH1408-H2 6743
HOH1409-O 6744
HOH1409-H1 6745
HOH1409-H2 6746
HOH1410-O 6747
HOH1410-H1 6748
HOH1410-H2 6749
HOH1411-O 6750
HOH1411-H1 6751
HOH1411-H2 6752
HOH1412-O 6753
HOH1412-H1 6754
HOH1412-H2 6755
HOH1413-O 6756
HOH1413-H1 6757
HOH1413-H2 6758
HOH1414-O 6759
HOH1414-H1 6760
HOH1414-H2 6761
HOH1415-O 6762
HOH1415-H1 6763
HOH1415-H2 6764
HOH1416-O 6765
HOH1416-H1 6766
HOH1416-H2 6767
HOH1417-O 6768
HOH1417-H1 6769
HOH1417-H2 6770
HOH1418-O 6771
HOH1418-H1 6772
HOH1418-H2 6773
HOH1419-O 6774
HOH1419-H1 6775
HOH1419-H2 6776
HOH1420-O 6777
HOH1420-H1 6778
HOH1420-H2 6779
HOH1421-O 6780
HOH1421-H1 67

...

HOH26280-H2 80960
HOH26281-O 80961
HOH26281-H1 80962
HOH26281-H2 80963
HOH26282-O 80964
HOH26282-H1 80965
HOH26282-H2 80966
HOH26283-O 80967
HOH26283-H1 80968
HOH26283-H2 80969
HOH26284-O 80970
HOH26284-H1 80971
HOH26284-H2 80972
HOH26285-O 80973
HOH26285-H1 80974
HOH26285-H2 80975
HOH26286-O 80976
HOH26286-H1 80977
HOH26286-H2 80978
HOH26287-O 80979
HOH26287-H1 80980
HOH26287-H2 80981
HOH26288-O 80982
HOH26288-H1 80983
HOH26288-H2 80984
HOH26289-O 80985
HOH26289-H1 80986
HOH26289-H2 80987
HOH26290-O 80988
HOH26290-H1 80989
HOH26290-H2 80990
HOH26291-O 80991
HOH26291-H1 80992
HOH26291-H2 80993
HOH26292-O 80994
HOH26292-H1 80995
HOH26292-H2 80996
HOH26293-O 80997
HOH26293-H1 80998
HOH26293-H2 80999
HOH26294-O 81000
HOH26294-H1 81001
HOH26294-H2 81002
HOH26295-O 81003
HOH26295-H1 81004
HOH26295-H2 81005
HOH26296-O 81006
HOH26296-H1 81007
HOH26296-H2 81008
HOH26297-O 81009
HOH26297-H1 81010
HOH26297-H2 81011
HOH26298-O 81012
HOH26298-H1 81013
HOH26298-H2 81014
HOH26299-O 81015
HOH26299-H1

HOH27119-O 83460
HOH27119-H1 83461
HOH27119-H2 83462
HOH27120-O 83463
HOH27120-H1 83464
HOH27120-H2 83465
HOH27121-O 83466
HOH27121-H1 83467
HOH27121-H2 83468
HOH27122-O 83469
HOH27122-H1 83470
HOH27122-H2 83471
HOH27123-O 83472
HOH27123-H1 83473
HOH27123-H2 83474
HOH27124-O 83475
HOH27124-H1 83476
HOH27124-H2 83477
HOH27125-O 83478
HOH27125-H1 83479
HOH27125-H2 83480
HOH27126-O 83481
HOH27126-H1 83482
HOH27126-H2 83483
HOH27127-O 83484
HOH27127-H1 83485
HOH27127-H2 83486
HOH27128-O 83487
HOH27128-H1 83488
HOH27128-H2 83489
HOH27129-O 83490
HOH27129-H1 83491
HOH27129-H2 83492
HOH27130-O 83493
HOH27130-H1 83494
HOH27130-H2 83495
HOH27131-O 83496
HOH27131-H1 83497
HOH27131-H2 83498
HOH27132-O 83499
HOH27132-H1 83500
HOH27132-H2 83501
HOH27133-O 83502
HOH27133-H1 83503
HOH27133-H2 83504
HOH27134-O 83505
HOH27134-H1 83506
HOH27134-H2 83507
HOH27135-O 83508
HOH27135-H1 83509
HOH27135-H2 83510
HOH27136-O 83511
HOH27136-H1 83512
HOH27136-H2 83513
HOH27137-O 83514
HOH27137-H1 83515
HOH27137-H2

HOH27874-O 85710
HOH27874-H1 85711
HOH27874-H2 85712
HOH27875-O 85713
HOH27875-H1 85714
HOH27875-H2 85715
HOH27876-O 85716
HOH27876-H1 85717
HOH27876-H2 85718
HOH27877-O 85719
HOH27877-H1 85720
HOH27877-H2 85721
HOH27878-O 85722
HOH27878-H1 85723
HOH27878-H2 85724
HOH27879-O 85725
HOH27879-H1 85726
HOH27879-H2 85727
HOH27880-O 85728
HOH27880-H1 85729
HOH27880-H2 85730
HOH27881-O 85731
HOH27881-H1 85732
HOH27881-H2 85733
HOH27882-O 85734
HOH27882-H1 85735
HOH27882-H2 85736
HOH27883-O 85737
HOH27883-H1 85738
HOH27883-H2 85739
HOH27884-O 85740
HOH27884-H1 85741
HOH27884-H2 85742
HOH27885-O 85743
HOH27885-H1 85744
HOH27885-H2 85745
HOH27886-O 85746
HOH27886-H1 85747
HOH27886-H2 85748
HOH27887-O 85749
HOH27887-H1 85750
HOH27887-H2 85751
HOH27888-O 85752
HOH27888-H1 85753
HOH27888-H2 85754
HOH27889-O 85755
HOH27889-H1 85756
HOH27889-H2 85757
HOH27890-O 85758
HOH27890-H1 85759
HOH27890-H2 85760
HOH27891-O 85761
HOH27891-H1 85762
HOH27891-H2 85763
HOH27892-O 85764
HOH27892-H1 85765
HOH27892-H2

HOH28629-H2 87959
HOH28630-O 87960
HOH28630-H1 87961
HOH28630-H2 87962
HOH28631-O 87963
HOH28631-H1 87964
HOH28631-H2 87965
HOH28632-O 87966
HOH28632-H1 87967
HOH28632-H2 87968
HOH28633-O 87969
HOH28633-H1 87970
HOH28633-H2 87971
HOH28634-O 87972
HOH28634-H1 87973
HOH28634-H2 87974
HOH28635-O 87975
HOH28635-H1 87976
HOH28635-H2 87977
HOH28636-O 87978
HOH28636-H1 87979
HOH28636-H2 87980
HOH28637-O 87981
HOH28637-H1 87982
HOH28637-H2 87983
HOH28638-O 87984
HOH28638-H1 87985
HOH28638-H2 87986
HOH28639-O 87987
HOH28639-H1 87988
HOH28639-H2 87989
HOH28640-O 87990
HOH28640-H1 87991
HOH28640-H2 87992
HOH28641-O 87993
HOH28641-H1 87994
HOH28641-H2 87995
HOH28642-O 87996
HOH28642-H1 87997
HOH28642-H2 87998
HOH28643-O 87999
HOH28643-H1 88000
HOH28643-H2 88001
HOH28644-O 88002
HOH28644-H1 88003
HOH28644-H2 88004
HOH28645-O 88005
HOH28645-H1 88006
HOH28645-H2 88007
HOH28646-O 88008
HOH28646-H1 88009
HOH28646-H2 88010
HOH28647-O 88011
HOH28647-H1 88012
HOH28647-H2 88013
HOH28648-O 88014
HOH28648-H1

HOH29468-O 90459
HOH29468-H1 90460
HOH29468-H2 90461
HOH29469-O 90462
HOH29469-H1 90463
HOH29469-H2 90464
HOH29470-O 90465
HOH29470-H1 90466
HOH29470-H2 90467
HOH29471-O 90468
HOH29471-H1 90469
HOH29471-H2 90470
HOH29472-O 90471
HOH29472-H1 90472
HOH29472-H2 90473
HOH29473-O 90474
HOH29473-H1 90475
HOH29473-H2 90476
HOH29474-O 90477
HOH29474-H1 90478
HOH29474-H2 90479
HOH29475-O 90480
HOH29475-H1 90481
HOH29475-H2 90482
HOH29476-O 90483
HOH29476-H1 90484
HOH29476-H2 90485
HOH29477-O 90486
HOH29477-H1 90487
HOH29477-H2 90488
HOH29478-O 90489
HOH29478-H1 90490
HOH29478-H2 90491
HOH29479-O 90492
HOH29479-H1 90493
HOH29479-H2 90494
HOH29480-O 90495
HOH29480-H1 90496
HOH29480-H2 90497
HOH29481-O 90498
HOH29481-H1 90499
HOH29481-H2 90500
HOH29482-O 90501
HOH29482-H1 90502
HOH29482-H2 90503
HOH29483-O 90504
HOH29483-H1 90505
HOH29483-H2 90506
HOH29484-O 90507
HOH29484-H1 90508
HOH29484-H2 90509
HOH29485-O 90510
HOH29485-H1 90511
HOH29485-H2 90512
HOH29486-O 90513
HOH29486-H1 90514
HOH29486-H2

In [79]:
htf.hybrid_system.getParticleMass(3150)

Quantity(value=4.0, unit=dalton)